<a href="https://colab.research.google.com/github/PranavPD7/Movie_Recommendation/blob/main/rating_prediction_using_sae.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import torch
import torch.nn as nn
import torch.nn.parallel
from torch.autograd import Variable
import pandas as pd
import numpy as np
import torch.utils.data
import torch.optim as optim

In [2]:
!unzip /content/ml-100k.zip -d /content/
!unzip /content/ml-1m.zip -d /content/

Archive:  /content/ml-100k.zip
   creating: /content/ml-100k/
  inflating: /content/ml-100k/allbut.pl  
  inflating: /content/ml-100k/mku.sh  
  inflating: /content/ml-100k/README  
  inflating: /content/ml-100k/u.data  
  inflating: /content/ml-100k/u.genre  
  inflating: /content/ml-100k/u.info  
  inflating: /content/ml-100k/u.item  
  inflating: /content/ml-100k/u.occupation  
  inflating: /content/ml-100k/u.user  
  inflating: /content/ml-100k/u1.base  
  inflating: /content/ml-100k/u1.test  
  inflating: /content/ml-100k/u2.base  
  inflating: /content/ml-100k/u2.test  
  inflating: /content/ml-100k/u3.base  
  inflating: /content/ml-100k/u3.test  
  inflating: /content/ml-100k/u4.base  
  inflating: /content/ml-100k/u4.test  
  inflating: /content/ml-100k/u5.base  
  inflating: /content/ml-100k/u5.test  
  inflating: /content/ml-100k/ua.base  
  inflating: /content/ml-100k/ua.test  
  inflating: /content/ml-100k/ub.base  
  inflating: /content/ml-100k/ub.test  
Archive:  /conten

In [4]:
#ti check movie names for corresponding movie ids check this
movies=training_set=pd.read_csv("/content/ml-1m/movies.dat",header=None,delimiter="::",encoding='latin1')
movies

<ipython-input-4-99929ff1bd82>:2: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  movies=training_set=pd.read_csv("/content/ml-1m/movies.dat",header=None,delimiter="::",encoding='latin1')


0                                   1                             2
0        1                    Toy Story (1995)   Animation|Children's|Comedy
1        2                      Jumanji (1995)  Adventure|Children's|Fantasy
2        3             Grumpier Old Men (1995)                Comedy|Romance
3        4            Waiting to Exhale (1995)                  Comedy|Drama
4        5  Father of the Bride Part II (1995)                        Comedy
...    ...                                 ...                           ...
3878  3948             Meet the Parents (2000)                        Comedy
3879  3949          Requiem for a Dream (2000)                         Drama
3880  3950                    Tigerland (2000)                         Drama
3881  3951             Two Family House (2000)                         Drama
3882  3952               Contender, The (2000)                Drama|Thriller

[3883 rows x 3 columns]

In [6]:
training_set=pd.read_csv("/content/ml-100k/u1.base",delimiter="\t")
test_set=pd.read_csv("/content/ml-100k/u1.test",delimiter="\t")
training_set=np.array(training_set,dtype='int')
test_set=np.array(test_set,dtype='int')
print("train:",training_set)


train: [[        1         2         3 876893171]
 [        1         3         4 878542960]
 [        1         4         3 876893119]
 ...
 [      943      1188         3 888640250]
 [      943      1228         3 888640275]
 [      943      1330         3 888692465]]


In [7]:
nb_users=int(max(max(training_set[:,0]),max(test_set[:,0])))
nb_movies=int(max(max(training_set[:,1]),max(test_set[:,1])))
print(nb_users,nb_movies)

943 1682


In [8]:
def convert(data):
  new_data=[]
  for id_users in range(1,nb_users+1):
    id_movies=data[:,1][data[:,0]==id_users]
    id_ratings=data[:,2][data[:,0]==id_users]
    ratings=np.zeros(nb_movies)
    ratings[id_movies-1]=id_ratings
    new_data.append(list(ratings))
  return new_data


In [9]:
training_set=convert(training_set)
test_set=convert(test_set)


In [10]:
print(test_set)

[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 3.0, 0.0, 5.0, 0.0, 5.0, 0.0, 0.0, 3.0, 0.0, 0.0, 4.0, 0.0, 0.0, 4.0, 3.0, 0.0, 0.0, 2.0, 0.0, 0.0, 0.0, 3.0, 0.0, 4.0, 0.0, 0.0, 2.0, 0.0, 0.0, 4.0, 0.0, 0.0, 0.0, 0.0, 5.0, 0.0, 0.0, 4.0, 0.0, 3.0, 0.0, 4.0, 0.0, 3.0, 3.0, 0.0, 4.0, 0.0, 0.0, 0.0, 5.0, 4.0, 3.0, 0.0, 5.0, 4.0, 0.0, 3.0, 0.0, 3.0, 3.0, 0.0, 4.0, 3.0, 1.0, 0.0, 4.0, 0.0, 1.0, 0.0, 4.0, 5.0, 5.0, 0.0, 4.0, 3.0, 5.0, 0.0, 0.0, 0.0, 4.0, 5.0, 3.0, 0.0, 0.0, 0.0, 5.0, 3.0, 4.0, 0.0, 5.0, 0.0, 2.0, 1.0, 1.0, 0.0, 0.0, 4.0, 5.0, 0.0, 0.0, 0.0, 1.0, 5.0, 5.0, 0.0, 0.0, 3.0, 3.0, 0.0, 1.0, 4.0, 0.0, 0.0, 0.0, 3.0, 0.0, 0.0, 4.0, 5.0, 3.0, 0.0, 4.0, 0.0, 4.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 1.0, 0.0, 2.0, 0.0, 0.0, 2.0, 0.0, 5.0, 4.0, 0.0, 0.0, 5.0, 2.0, 0.0, 4.0, 0.0, 3.0, 4.0, 4.0, 0.0, 4.0, 3.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.0, 5.0, 0.0, 0.0, 5.0, 5.0, 0.0, 5.0, 0.0, 0.0, 3.0, 0.0, 0.0, 5.0, 4.0, 4.0, 4.0, 0.0, 3.0, 3.0, 5.0, 0.0, 0.0, 4.0, 0.0, 0.0, 5.0, 0.0, 0.0, 0.0, 3.0

In [11]:
training_set=torch.FloatTensor(training_set)
test_set=torch.FloatTensor(test_set)

In [12]:
class SAE(nn.Module):
  def __init__(self, ):
    super(SAE,self).__init__()
    self.fc1=nn.Linear(nb_movies,20)
    self.fc2=nn.Linear(20,10)
    self.fc3=nn.Linear(10,20)
    self.fc4=nn.Linear(20,nb_movies)
    self.activation=nn.Sigmoid()
  def forward(self,x):
    x=self.activation(self.fc1(x))
    x=self.activation(self.fc2(x))
    x=self.activation(self.fc3(x))
    x=self.fc4(x)
    return x
sae=SAE()
criterion=nn.MSELoss()
optimizer=optim.RMSprop(sae.parameters(),lr=0.01,weight_decay=0.5)





In [13]:
nb_epoch=200
for epoch in range(1,nb_epoch+1):
  train_loss=0
  s=0.
  for id_users in range(nb_users):
    inputs=Variable(training_set[id_users]).unsqueeze(0)
    target=inputs.clone()
    if torch.sum(target.data>0)>0:
      output=sae(inputs)
      target.require_grad=False
      output[target==0]=0
      loss=criterion(output,target)
      mean_corrector=nb_movies/float(torch.sum(target.data>0)+1e-10)
      loss.backward()
      train_loss+=np.sqrt(loss.item()*mean_corrector)
      s+=1.
      optimizer.step()
  print("epoch:"+str(epoch)+"loss:"+str(train_loss/s))

epoch:1loss:1.7719956992661663
epoch:2loss:1.096746266855009
epoch:3loss:1.0533420821228572
epoch:4loss:1.0384229958208
epoch:5loss:1.030754821989252
epoch:6loss:1.0267469858544087
epoch:7loss:1.023783383427048
epoch:8loss:1.0217365225143247
epoch:9loss:1.0207438129290047
epoch:10loss:1.0196836189941823
epoch:11loss:1.0191833678505655
epoch:12loss:1.0181929668067802
epoch:13loss:1.0179499148109274
epoch:14loss:1.0175416442863803
epoch:15loss:1.0174570291212608
epoch:16loss:1.0170189106648493
epoch:17loss:1.016561361113409
epoch:18loss:1.0165877534122358
epoch:19loss:1.0166644609513578
epoch:20loss:1.0162005785607509
epoch:21loss:1.0159577424155195
epoch:22loss:1.0161183964247482
epoch:23loss:1.015833056808613
epoch:24loss:1.015714696611697
epoch:25loss:1.0160051964906969
epoch:26loss:1.0155600273000185
epoch:27loss:1.0155603093040593
epoch:28loss:1.0149453550380685
epoch:29loss:1.0123613694151938
epoch:30loss:1.011038498409736
epoch:31loss:1.0095462132589617
epoch:32loss:1.007167109993

In [14]:
test_loss=0
s=0.
for id_users in range(nb_users):
  inputs=Variable(training_set[id_users]).unsqueeze(0)
  target=Variable(test_set[id_users]).unsqueeze(0)
  if torch.sum(target.data>0)>0:
    output=sae(inputs)
    target.require_grad=False
    output[target==0]=0
    loss=criterion(output,target)
    mean_corrector=nb_movies/float(torch.sum(target.data>0)+1e-10)
    test_loss+=np.sqrt(loss.item()*mean_corrector)
    s+=1.

print("loss:"+str(test_loss/s))

loss:0.9490508286500459


In [15]:
# input("enter ratings of movie u have watched in a list at the corresponding indexes")
# movie=input("enter movie whose rating u want to predict")


tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        ...,
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]])